<a href="https://colab.research.google.com/github/MTRL-studio/mtrl-3d-scripts/blob/main/models/colab/design_template_colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# FullControl design template

*<<< check out demo models [here](https://github.com/FullControlXYZ/fullcontrol/tree/master/models/README.md) >>>*
  
press ctrl+F9 to run all cells in this notebook, or press shift+enter to run each cell sequentially

if you change one of the code cells, make sure you run it and all subsequent cells again (in order)

*this document is a jupyter notebook - if they're new to you, check out how they work: [link](https://www.google.com/search?q=ipynb+tutorial), [link](https://jupyter.org/try-jupyter/retro/notebooks/?path=notebooks/Intro.ipynb), [link](https://colab.research.google.com/)*
### be patient :)

the next code cell may take a while because running it causes several things to happen:
- connect to a google colab server -> download the fullcontrol code -> install the fullcontrol code

check out [other tutorials](https://github.com/FullControlXYZ/fullcontrol/blob/master/tutorials/README.md) to understand the python code for the FullControl design

In [10]:
if 'google.colab' in str(get_ipython()):
  !pip install git+https://github.com/FullControlXYZ/fullcontrol --quiet
import fullcontrol as fc
from google.colab import files

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [12]:
# printer/gcode parameters

design_name = 'my_design'
nozzle_temp = 210
bed_temp = 55
print_speed = 8000
fan_percent = 100
printer_name='bambulab_x1' # generic / ultimaker2plus / prusa_i3 / ender_3 / cr_10 / bambulab_x1 / toolchanger_T0

In [13]:
import math

# --- 1. Printer Settings (Optimized for Bambu X1 0.4mm nozzle) ---
EW = 0.45          # Extrusion Width (0.45 is strong for single-wall vases)
EH = 0.2           # Layer Height (Standard quality)
initial_z = EH*0.6 # Squish for bed adhesion

# --- 2. Scale & Dimensions ---
SCALE = 3.0        # 300% Scale
base_radius = 15   # Original radius of the demo model
base_height = 40   # Original height of the demo model

# Calculate the new real-world dimensions
radius = base_radius * SCALE
total_height = base_height * SCALE

# Automatically calculate how many layers strictly based on height
# This replaces the hardcoded "layers = 50"
layers = int(total_height / EH)

# --- 3. Ripple Texture Settings ---
# You can tweak these to change the "Organic Modern" look
ripples_per_layer = 12   # Number of bumps around the circle
ripple_amplitude = 2.0   # Depth of the texture in mm
twist_angle = 0.2        # How much the pattern spirals up

In [14]:
steps = []

# Points per layer (higher radius needs more points for smooth curves)
steps_per_layer = int(100 * SCALE)

for layer in range(layers):
    # Calculate exact Z height for this layer
    current_z = (layer * EH) + initial_z

    # Create one full circle (loop)
    for i in range(steps_per_layer):
        # Percentage around the circle (0.0 to 1.0)
        t = i / steps_per_layer
        angle = t * 2 * math.pi

        # --- THE RIPPLE MATH ---
        # 1. Create the base wave based on angle
        # 2. Add a phase shift based on Z height (layer) to make it twist/spiral
        phase_shift = layer * twist_angle

        # Calculate the offset for this specific point
        offset = ripple_amplitude * math.sin((angle * ripples_per_layer) + phase_shift)

        # Apply offset to the radius
        current_radius = radius + offset

        # Convert Polar (Angle/Radius) to Cartesian (X/Y)
        x = current_radius * math.cos(angle)
        y = current_radius * math.sin(angle)

        steps.append(fc.Point(x=x, y=y, z=current_z))

In [15]:
# preview the design
# This generates the 3D visualizer.
# Rotate with your mouse to check the "Organic Modern" ripples.

fc.transform(steps, 'plot', fc.PlotControls(style='line', zoom=0.7))

In [ ]:
# generate and save gcode
gcode_controls = fc.GcodeControls(
    printer_name=printer_name, # Pulls 'bambulab_x1' from Section 2
    initialization_data={
        'print_speed': print_speed,
        'nozzle_temp': nozzle_temp,
        'bed_temp': bed_temp,
        'fan_percent': fan_percent,
        'extrusion_width': EW,
        'extrusion_height': EH
    }
)

gcode = fc.transform(steps, 'gcode', gcode_controls)
filename = f'{design_name}.gcode'
with open(filename, 'w') as f:
    f.write(gcode)

print(f"Success! Downloaded {filename}")
files.download(filename)

#### please tell us what you're doing with FullControl!

- tag FullControlXYZ on social media ([twitter](https://twitter.com/FullControlXYZ), [instagram](https://www.instagram.com/fullcontrolxyz/), [linkedin](https://www.linkedin.com/in/andrew-gleadall-068587119/), [tiktok](https://www.tiktok.com/@fullcontrolxyz))
- email [info@fullcontrol.xyz](mailto:info@fullcontrol.xyz)
- post on the [subreddit](https://reddit.com/r/fullcontrol)
- post in the [github discussions or issues tabs](https://github.com/FullControlXYZ/fullcontrol/issues)

in publications, please cite the original FullControl paper and the github repo for the new python version:

- Gleadall, A. (2021). FullControl GCode Designer: open-source software for unconstrained design in additive manufacturing. Additive Manufacturing, 46, 102109.
- Gleadall, A. and Leas, D. (2023). FullControl [electronic resource: python source code]. available at: https://github.com/FullControlXYZ/fullcontrol